In [40]:
import folium
from folium.plugins import MarkerCluster
import geopandas as gpd
import pandas as pd

In [41]:
# Read in UK Historical Plaques data
plaques_df = pd.read_json("https://s3.eu-west-2.amazonaws.com/openplaques/open-plaques-United-Kingdom-2021-06-26.json").dropna().drop('updated_at', axis=1)

plaques = gpd.GeoDataFrame(
    plaques_df, geometry=gpd.points_from_xy(plaques_df.longitude, plaques_df.latitude, crs=4326)
)

plaques_df = None
# plaques.head()

In [42]:
# Read in London boroughs data
boroughs = gpd.read_file("https://skgrange.github.io/www/data/london_boroughs.json")
# boroughs.head()

In [43]:
# Find the number of plaques in each borough
boroughs = boroughs.join(
            gpd.sjoin(plaques, boroughs).groupby("index_right").size().rename("numPlaques"),
            how="left",
        )

In [44]:
# Calculate the plaque density
boroughs['area_sqkm'] = boroughs['area_hectares'] / 100
boroughs['PlaqueDensity_sqkm'] = boroughs['numPlaques'] / boroughs['area_sqkm'] 

In [45]:
# Initialize map over London
map = folium.Map(location=[51.507351, -0.127758], tiles="Stamen Toner", zoom_start=10, height='90%', prefer_canvas=True)

# Add a title
title_html = '''
             <h5 align="center"; margin-bottom=0px; padding-bottom=0px; style="font-size:20px"><b>Historical Plaques of London</b></h3>
             <h5 align="center"; margin-top=0px; padding-top=0px; style="font-size:14px">Click on the blue circles for more info</h3>
             '''

map.get_root().html.add_child(folium.Element(title_html))

In [46]:
# Create a marker for each plaque location. Format popup

marker_cluster = MarkerCluster().add_to(map)

for index, row in plaques.iterrows():
    html = f"""<strong>Title:</strong> {row['title']}<br>
        <br>
        <strong>Inscription:</strong> {row['inscription']}<br>
        <br>
        <strong>Erected:</strong> {row['erected_at']}<br>
        <br>
        Find more info <a href={row['uri']} target="_blank">here</a><br>
            """
        
    iframe = folium.IFrame(html,
                       width=200,
                       height=200)

    popup = folium.Popup(iframe,
                     max_width=400)
    

    folium.CircleMarker(location=[row["latitude"], row["longitude"]],
                                            radius=10,
                                            color="#3186cc",
                                            fill=True,
                                            fill_color="#3186cc",
                                            popup=popup).add_to(marker_cluster)

    

In [47]:
# Choropleth styling
import branca.colormap as bcm

# Create color map
# "Fall" color ramp from https://carto.com/carto-colors/

scale = (boroughs['PlaqueDensity_sqkm'].quantile((0, 0.02, 0.5, 0.9, 0.98, 1))).tolist()

colormap = bcm.LinearColormap(colors=['#008080','#70a494', '#b4c8a8', '#edbb8a', '#de8a5a','#ca562c'], 
    index=scale,
    vmin=min(boroughs['PlaqueDensity_sqkm']),
    vmax=max(boroughs['PlaqueDensity_sqkm']))

style_function = lambda x: {
    'fillColor': colormap(x['properties']['PlaqueDensity_sqkm']),
    'color': 'black',
    'weight': 1.5,
    'fillOpacity': 0.3
}

In [48]:
# Plot choropleth layer
folium.GeoJson(
    boroughs,
    style_function=style_function,
    tooltip=folium.GeoJsonTooltip(
        fields=['name', 'numPlaques'],
        aliases=['Borough', 'Historic Markers'],
        localize=True
    )
).add_to(map)

colormap.caption = 'Historic markers per sq. km'
colormap.add_to(map)

In [49]:
map

In [217]:
map.save("./index.html")

with open("./UK-plaques-2021-06-26.json", "w") as outfile:
    outfile.write(plaques.to_json())

boroughs.to_file("./london-boroughs.geojson", driver="GeoJSON")

c:\Anaconda3\envs\gis_workbench\lib\site-packages\geopandas\io\file.py:362: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  pd.Int64Index,
